# Waveforms import and charge spectrum

_This notebook allow you to read waveform files, e.g. acquired with the Lecroy oscilloscopes, and to make a charge spectrum of a set of waveforms by integrating the signals within a fixed time window (correcting for baseline)_

### Table of content

You can open the table of contents as sidebar either from the `View` menu or by pressing `Ctrl+Shift+K`

# Setup

## Graphics setup

When `%jsroot` is `on`, most of the displayed graphics is interactive.
Without, all the plots are static images, which may be useful when:
 - a lot of interactive plots slow down the browser
 - you want to export to formats e.g. PDF that requires static images 

In [1]:
%jsroot on
//%jsroot off

In [2]:
TCanvas c1("c1","c1",1000,400);
//c1.SetCanvasSize(1200,300);
//c1.Size(20.,5.);

## Code setup (probably nothing to change here)

The {fmt} library is used to have easier string formatting and pretty-print.


In [3]:
gSystem->Load("/cvmfs/sfrsbi.gsi.de/debian12/2025/fmt11_1_2/lib/libfmt.so")    //if the system provides {fmt} as compiled library

(int) 0


In [4]:
//#define FMT_HEADER_ONLY
// The previous #define is required before the following includes in case the system does NOT provide {fmt} as compiled library (lower performance)
#include "/cvmfs/sfrsbi.gsi.de/debian12/2025/fmt11_1_2/include/fmt/core.h"
#include "/cvmfs/sfrsbi.gsi.de/debian12/2025/fmt11_1_2/include/fmt/ranges.h"
#include "/cvmfs/sfrsbi.gsi.de/debian12/2025/fmt11_1_2/include/fmt/color.h"



The code to read the waveform files is taken from an include file (please do not modify it).

In [5]:
#include "/u/sfsexp/DetTests/SfrsSci/PmtCalib/LecroyDecoder.hpp"

## Setup analysis parameters

### Waveform files data-taking conditions

Add string-key/double-value pairs to this `std::map` to save the conditions in which the data-taking was performed. At the end of the analysis, results will be added here as additional key/value pairs and then everything will be written on a text file.

In [6]:
std::map<std::string, double> list_setup_and_results;
std::string pmt_serial_code = "AGG001"; //the output text file will have the serial code in the name

list_setup_and_results[ "HV" ] = 0.86;
//list_setup_and_results[ "LED" ] = 1; //unfortunately only double values... 1 for SPE, > 1 for high illumination
list_setup_and_results[ "LED" ] = 20; // > 1 for higher illumination (use different values for two different LED light intensities)


### Waveform files path

Here you should provide the names of the files from which the waveforms should be loaded. Since they usually differ by a five digit counter in the name, you can just setup the first and last number, and optionally an exclude list and a list of names will be generated for you. Fill the variables in the next cell (Note the `--FILL HERE--` in the comments):

In [7]:
namespace fs = std::filesystem; //added in C++17

// --FILL HERE-- the directory and the file name template
fs::path source_data_dir{ "/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/" };
constexpr const char* filename_template = "C1--AGG001lowscan0V86--{:05}.trc"; //leave the {:05} format specifier where the counter is

// --FILL HERE-- the first and last (included) file number and optionally some exclusion
unsigned int first_file_counter {0};
unsigned int last_file_counter {10}; //the last is INCLUDED
std::vector<unsigned int> excluded_file_counters = {}; //comma separated list, e.g. {3, 55, 111,}

//let's put the list in good order and without duplicates
std::sort( excluded_file_counters.begin(), excluded_file_counters.end() );
excluded_file_counters.erase( std::unique( excluded_file_counters.begin() , excluded_file_counters.end() ), 
                              excluded_file_counters.end() ); //yes, unique() requires erase() afterwords, google for it if you wonder why

#### Waveform files copy to local folders (if needed)

It might be that the data files are not yet located in a local folder and you want to copy them e.g. from the zip files in the `/lustre` archive.

These are some guidelines for commands that you can run on a terminal to achieve this (you can also open a terminal from the main jupyter interface and have it within your browser).

  * If the `sshfs` tunnel to the `/lustre` archive directory is not mounted (e.g. `to_lustre_archive` is a normal, empty directory), you can mount it with:

```bash
    sfsexp@lxiXYZ:~$ sshfs sfsexp@lustre.hpc.gsi.de:/lustre/sfrs/SfrsScintillators/PmtCalib to_lustre_archive
```

  * Whenever you want to close this tunnel you can:

```bash
    sfsexp@lxiXYZ:~$ fusermount -u to_lustre_archive
```

  * To unzip the archive on `/lustre` to a temporary local folder (all GSI nodes have a `/data.local1/` local not-backed-up directory, typically the internal hard disk, with free access for any user), you can

```bash
    sfsexp@lxiXYZ:~$ mkdir -p /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir
    sfsexp@lxiXYZ:~$ cd /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir
    sfsexp@lxiXYZ:~$ unzip ~/to_lustre_archive/RawWaveformsArchive/AGG001.zip
```

### Waveform integration parameters

Specify the integration ranges for baseline and signal. Later on these ranges will be shown in the waveforms plots as coloured background, so you can go back to this cell if you are not satisfied of the choice, and run the cell again with corrected ranges.

In [8]:
// --FILL HERE-- integration range for the signals and for the baseline
unsigned int first_baseline_sample = 100;
unsigned int first_not_included_baseline_sample = 900;
unsigned int first_signal_sample = 900;
unsigned int first_not_included_signal_sample = 2500;

TBox box_baseline{ first_baseline_sample*1., 0., first_not_included_baseline_sample*1., 1.};
box_baseline.SetFillColorAlpha(kAzure, 0.05);
TBox box_signal{ first_signal_sample*1., 0., first_not_included_signal_sample*1., 1.};
box_signal.SetFillColorAlpha(kSpring, 0.05);

double integration_interval_ratio = (first_not_included_signal_sample - first_signal_sample);
integration_interval_ratio /= (first_not_included_baseline_sample - first_baseline_sample)

(double) 2.0000000


## Check setup

First of all, a first check is made that the HV specified in `list_setup_and_results[ "HV" ]` seems consistent with the `filename_template` (it can often happen that one forget to update one of the two)

In [9]:
// Just a simple attempt to catch most usual overlooks, usually filename_template has the HV in the 
// name, with 'V' instead of the dot

{           //in a block to not pollute the notebook with additional variables
    auto HV_as_string = fmt::format( "{:.2}", list_setup_and_results["HV"] );
    std::replace( HV_as_string.begin(), HV_as_string.end(), '.', 'V' );
    if (std::string_view(filename_template).find(HV_as_string) == std::string_view::npos)
        fmt::print(fmt::fg(fmt::color::red), 
            "\n!!! Provided HV setting does not seem to match with the waveforms filenames. Have you made any mistake?\n\n");
}

Then the file names are produced and each file is checked for existence, then a report is produced

In [10]:
std::vector<std::string> list_of_filenames; 
list_of_filenames.reserve(last_file_counter+1-first_file_counter);

for (int jfile = first_file_counter; jfile <= last_file_counter; ++jfile) {
    if (std::binary_search( excluded_file_counters.begin() , excluded_file_counters.end() , jfile )) continue;
    
    fs::path file_path = source_data_dir / fmt::format(filename_template , jfile);
    if (fs::is_regular_file( file_path )) {
        list_of_filenames.push_back( file_path.string() );
    } else {
        fmt::print("Error: the file {} does not exists or is not a regular file\n", file_path.string() );
    }
}
for (const auto& filename : list_of_filenames) fmt::print("{}\n", filename);

/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00000.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00001.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00002.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00003.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00004.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00005.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00006.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00007.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00008.trc
/data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00009.trc
/data.local1/sfsexp/DetTests/S

One file (e.g. the first) is open to check waveform details like horizontal/vertical scale, etc., and if waveform samples can be accessed.

A warning is emitted if the number of samples composing the waveform is smaller than the integration ranges chosen earlier (you should not continue without correcting the ranges, or the next cells will crash or provide wrong results)

In [11]:
using samples_type = int16_t;

WfLecroyBinaryDecoder<samples_type> ch1dec( list_of_filenames[0] );
std::vector<samples_type> ch1;
float vscale1, voffset1;
auto success = ch1dec.ProvideVerticalScale(vscale1) && ch1dec.ProvideVerticalOffset(voffset1) ;
float sampling_interval1 = ch1dec.header.horizontal_interval; // accessor not yet added, so the header is kept public
// This is how you would extract the horizontal offset from the misaligned data words. But this quantity is usually not needed 
double ch1dec_horiz_offset;
std::memcpy(&ch1dec_horiz_offset, &ch1dec.header.horizontal_offset, sizeof(double));
// Let's check if also samples (e.g. for the first waveform) can be accessed
ch1dec.ProvideSamples(ch1,1,0);
success = success && ch1dec.ifsWf.good();
    
if (success) {
    fmt::print("\nSuccessfully decoded one waveform file. Waveforms have {} samples and:\n\n"
        "\t{:10.8} mV vertical resolution, \t{:8.3} mV vertical offset\n"
        "\t{:10.3} ns sampling interval, \t{:8.3} ns time offset\n\n",
        ch1.size(),
        vscale1*1.e3f, voffset1*1.e3f, sampling_interval1*1.e9f, ch1dec_horiz_offset*1.e9f);
    if (ch1.size() < first_not_included_signal_sample)
        fmt::print(fmt::bg(fmt::color::red)|fmt::fg(fmt::color::yellow),
            "ERROR: The waveform has not enough samples for the chosen integration ranges! Go back and correct them!\n");
} else {
    fmt::print(fmt::fg(fmt::color::red), "The decoding of the waveform file failed\n");
}


Successfully decoded one waveform file. Waveforms have 4002 samples and:

	 0.0274624 mV vertical resolution, 	     650 mV vertical offset
	      0.05 ns sampling interval, 	   -15.6 ns time offset



### Check also some waveforms, e.g. from the first file

Here you can also check graphically if the chosen integration intervals for baseline and signal match your expectations.

Two ways to look at multiple waveforms in one plot are presented:
  * Cumulating all waveforms in the same histogram by sample id, useful to emphasize recurring features at specific times
  * Overlapping all waveform in the same 2D histogram, to see real wavefom amplitudes (by converting the scales with the proper factor)

You can also edit the cells to consider only few waveforms etc... or commenting it out because it is time consuming

In [12]:
TH1F h1ch1("","All Waveforms summed up; Sample time (s); A.U.",ch1.size(), 0. , 1.*ch1.size());
h1ch1.SetStats(false);

//ch1dec.ChangeFile( list_of_filenames[42] );          // if you want to check another file

///*                                                   // if you want to comment out because is time-consuming
{                                                      // in a block so that local variables like k do not pollute the environment 
  int k = 0;
  while ( ch1dec.ProvideSamples(ch1,1,k++) )
  //if ( ch1dec.ProvideSamples(ch1,1,k++) )
    for (int j = 1; auto s : ch1)
      h1ch1.AddBinContent(j++, s);
}
//*/

In [13]:
c1.Clear(); 
h1ch1.Draw("axis");
//Weird ROOT API... the DrawBox method actually draws a COPY of the original (which is unmodified) in a new position
box_baseline.DrawBox(box_baseline.GetX1() , h1ch1.GetMinimum() , box_baseline.GetX2() , h1ch1.GetMaximum());
box_signal.DrawBox(box_signal.GetX1() , h1ch1.GetMinimum() , box_signal.GetX2() , h1ch1.GetMaximum());
h1ch1.Draw("same");
c1.Draw()

In [14]:
TH2F h2ch1("","Overlapped raw waveforms; Time within waveform (ns); Amplitude (V)",
            ch1.size()/2, 0. , sampling_interval1*1.e9f*ch1.size(), 
            4096, -32768.*vscale1-voffset1, 32768.*vscale1-voffset1);
h2ch1.SetStats(false);

//ch1dec.ChangeFile( list_of_filenames[42] );          // if you want to check another file

///*                                                   // if you want to comment out because is time-consuming
{                                                      // in a block so that local variables like k do not pollute the environment 
  int k = 0;
  while ( ch1dec.ProvideSamples(ch1,1,k++) )
  //if ( ch1dec.ProvideSamples(ch1,1,k++) )
    for (int j = 0; auto s : ch1)
      h2ch1.Fill(sampling_interval1*1.e9f*j++, s*vscale1-voffset1);
}
//*/

In [15]:
c1.Clear(); 
h2ch1.Draw("zcol");
//Weird ROOT API... the DrawBox method actually draws a COPY of the original (unmodified) in a new position
box_baseline.DrawBox( box_baseline.GetX1()*sampling_interval1*1.e9f , -32768.*vscale1-voffset1 , 
                      box_baseline.GetX2()*sampling_interval1*1.e9f , 32768.*vscale1-voffset1);
box_signal.DrawBox( box_signal.GetX1()*sampling_interval1*1.e9f , -32768.*vscale1-voffset1 , 
                    box_signal.GetX2()*sampling_interval1*1.e9f , 32768.*vscale1-voffset1);
c1.Draw()

# Integrated charge spectra

The signal integrated charge is calculated in the selected sample intervals, subtracting the baseline contribution.
The baseline spectrum is also shown as cross-check.

**You must adapt here the histogram ranges** (look for `--CORRECT HERE--` in the comments)

You might also decide to filter out some events, maybe because the baseline is screwed up or something else weird has been observed in the waveform; 

In [20]:
// --CORRECT-- the histogram ranges --------------------------------------v here
TH1F h1ch1q("","Integrated charge spectrum; amount of e-",      500,     -50.e6 , 4950.e6);
TH1F h1ch1b("","Integrated baseline; amount of e-",             500,     -250.e6 , 250.e6);
TH1F h1ch1bf("","Integrated baseline (filtered); amount of e-", 500,     -250.e6 , 250.e6);
h1ch1bf.SetLineColor(kRed);

std::vector< std::set<int> > list_of_excluded_waveforms( list_of_filenames.size() ); //an empty std::set of indexes per waveform file
// e.g. to exclude the third, 25th and 107th waveform from the second file:
//list_of_excluded_waveforms[1].insert( {2, 24, 106, 12} );

The next cells fill now the histograms. If you go through the code, you can filter out some waveforms on the basis of their baseline integral or other criteria. Look for `--FILTER HERE--` comment fields.

In [21]:
// A class dealing with the statistics of a group of samples, used in the next cell
template <typename T>
class SamplesStats
{
    static_assert( std::is_arithmetic<T>::value );
public:
    SamplesStats( std::span<T> samples )
    : n{samples.size()}
    {
        for (auto s : samples) {
            sum += s;
            sum2 += s*s;
            if (s < min) min = s;
            if (s > max) max = s;
        }
    }

    double N() const { return n; }
    double Min() const { return min; }
    double Max() const { return max; }
    double Sum() const { return sum; }
    double Sum2() const { return sum; }
    double Mean() const
    { return (n>0)? sum/n : std::numeric_limits<double>::quiet_NaN(); }
    double Var() const 
    { return (n>1)? (sum2-sum*sum/n)/(n-1) : std::numeric_limits<double>::quiet_NaN(); }
    double StdDev() const { return std::sqrt(Var()); }

private:
    std::size_t n;
    double min { std::numeric_limits<double>::max() };
    double max { std::numeric_limits<double>::min() };
    double sum {0};
    double sum2 {0};
};

In [22]:
h1ch1q.Reset();
h1ch1b.Reset();
h1ch1bf.Reset();

{    // in a block so that local variables do not pollute the rest of the notebook
    auto FillHistos = []( const auto& samples )
    {
        //Check for out of bound
        if (samples.size() < std::max( std::max(first_baseline_sample , first_not_included_baseline_sample) , 
                                       std::max(first_signal_sample , first_not_included_signal_sample) ) )
            return;
        
        std::span baseline_span{samples.begin()+first_baseline_sample, 
                                samples.begin()+first_not_included_baseline_sample };
        std::span signal_span{  samples.begin()+first_signal_sample, 
                                samples.begin()+first_not_included_signal_sample };

        SamplesStats baseline{ baseline_span } , signal{ signal_span };
        
        // Calculate baseline, you can --FILTER HERE-- waveforms with bad baseline
        double bq = -( baseline.Sum()*vscale1 - voffset1*(first_not_included_baseline_sample-first_baseline_sample) )
                    / 50. * sampling_interval1 / 1.6e-19; // 50 ohm terminated line
        h1ch1b.Fill(bq);
        if ( std::abs(bq-(-46.2e6)) > 30e6 ) return;         // Maybe --FILTER HERE-- on the basis of the integral
        //if ( baseline.StdDev() > 9000. * 1.6e-19 / sampling_interval1 * 50 / vscale1 ) 
        //    return;                                          // Maybe --FILTER HERE-- on the basis of the std deviation
        if ( baseline.Max() > baseline.Mean()+5*baseline.StdDev() ||        // Maybe --FILTER HERE-- on the basis
            baseline.Min() < baseline.Mean()-5*baseline.StdDev()) return;   // of the presence of spikes
        h1ch1bf.Fill(bq);

        double integrated_signal = signal.Sum() - baseline.Sum() * integration_interval_ratio;
        double q = -( integrated_signal*vscale1 )            // voffset already subtracted by baseline subtraction
                    / 50.* sampling_interval1 / 1.6e-19;     // 50 ohm terminated line
        h1ch1q.Fill(q);
    };

    // Now the FillHisto() will be called for all not excluded waveforms in all files
    for (int jfile = -1; const auto& filename : list_of_filenames) {
        fmt::print( "Processing waveforms from {} (file index {})\n", filename, ++jfile);
        ch1dec.ChangeFile(filename);
    
        int k_wf = 0;

        for (auto excluded_wf : list_of_excluded_waveforms[jfile]) {
            while ( k_wf < excluded_wf && ch1dec.ProvideSamples( ch1, 1, k_wf++) 
                    && ch1.size() >= first_not_included_signal_sample )
                FillHistos( ch1 );
            fmt::print( "Skipping waveform {} in this file\n", k_wf);
            k_wf = excluded_wf + 1;
        }
        //The rest of the waveforms after the last excluded
        while ( ch1dec.ProvideSamples( ch1, 1, k_wf++) 
                && ch1.size() >= first_not_included_signal_sample )
            FillHistos( ch1 );
    }

}

Processing waveforms from /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00000.trc (file index 0)
Processing waveforms from /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00001.trc (file index 1)
Processing waveforms from /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00002.trc (file index 2)
Processing waveforms from /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00003.trc (file index 3)
Processing waveforms from /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00004.trc (file index 4)
Processing waveforms from /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00005.trc (file index 5)
Processing waveforms from /data.local1/sfsexp/DetTests/SfrsSci/PmtCalib/TmpDataDir/AGG001/C1--AGG001lowscan0V86--00006.trc (file index 6)
Processing waveforms from /data.lo

In [23]:
gStyle->SetOptStat(2112210);
gStyle->SetOptFit(1111);//gStyle->SetOptLogy();
c1.Clear(); c1.Divide(2,1);
c1.cd(1)->SetLogy(true); h1ch1b.Draw(); h1ch1bf.Draw("sames"); 
c1.cd(2)->SetLogy(true); h1ch1q.Draw();
c1.Draw()

_In case of a single photoelectron spectrum_, you can make a quick and dirty check that at least 95% of the events are empty 
by comparing the population of the pedestal with the total of the events (you can hover with the mouse on the plot - if `jsroot` is on - to decide until which bin of the histogram the event is pedestal

In [24]:
if (list_setup_and_results["LED"] == 1.) {
    // --CORRECT-- the bin number here  --------------------------|
    //                                                            V
    fmt::print("Empty events ratio: {}%\n", h1ch1q.Integral( 1 , 63 ) / h1ch1q.Integral() * 100.);
}

# Fit of the charge spectrum

Depending on the meaning of the charge spectrum, either a high illumination spectrum or a single photo-electron (SPE) spectrum, two different fit models must be applied. Furthermore, for the second case, the ROOFIT tool is used (as it has more advanced and useful features)

In both cases, the results of the fit collected so that in the last section can be saved to a file (you can use the Table of Contents to go straight to the last section after the fit)

## Fit for a high illumination spectrum

(skip this section if you have a SPE spectrum)

In [25]:
if (list_setup_and_results["LED"] > 1.) {
    auto fit_result = h1ch1q.Fit("gaus", "S","");
    c1.Clear();
    h1ch1q.Draw();

    list_setup_and_results[ "chi2" ] = fit_result->Chi2();
    list_setup_and_results[ "ndf" ] = fit_result->Ndf();
    list_setup_and_results[ fit_result->ParName(0) ] = fit_result->Parameter(0);
    list_setup_and_results[ fit_result->ParName(1) ] = fit_result->Parameter(1);
    list_setup_and_results[ fit_result->ParName(2) ] = fit_result->Parameter(2);
    list_setup_and_results[ (fit_result->ParName(0))+"_error" ] = fit_result->ParError(0);
    list_setup_and_results[ (fit_result->ParName(1))+"_error" ] = fit_result->ParError(1);
    list_setup_and_results[ (fit_result->ParName(2))+"_error" ] = fit_result->ParError(2);

    c1.Draw();
}

****************************************
Minimizer is Minuit2 / Migrad
Chi2                      =      158.327
NDf                       =           78
Edm                       =  2.06384e-08
NCalls                    =           59
Constant                  =       2147.8   +/-   11.2492     
Mean                      =  2.27233e+09   +/-   436916      
Sigma                     =  1.00799e+08   +/-   302966       	 (limited)


In [26]:
list_setup_and_results   

(std::map<std::string, double> &) { "Constant" => 2147.7995, "Constant_error" => 11.249246, "HV" => 0.86000000, "LED" => 20.000000, "Mean" => 2.2723337e+09, "Mean_error" => 436916.36, "Sigma" => 1.0079926e+08, "Sigma_error" => 302966.23, "chi2" => 158.32680, "ndf" => 78.000000 }


## Fit for a SPE spectrum

(skip in case of high illumination spectrum)

In this case we try to fit the spectrum with a combination of Gaussians for:
  * The **pedestal**, centered at zero since we corrected the baseline. Therefore, excluding the constant factor representing the amplitude (or the integral), the shape has a single free parameter, the $\sigma$ of the Gaussian shape.
  * The **single photo-electron peak**. This Gaussian, excluding again the constant factor representing the amplitude (or the integral), has two free parameters: the **mean**, usually referred as *the **gain** of the PMT*, and the Gaussian $\sigma$.
  * The **Two photo-electron peak**, in case of a relevent amount. The mean of this Gaussian is not a new independent parameter, but *it should be twice the mean of the SPE peak*. In principle also the $\sigma$ should be related to the SPE peak by a factor $\sqrt{2}$, but these are in reality the convolution of the spread of the dynodes exponential amplification process (which is btw *not* Gaussian) and the "measurement resolution": it can be modeled as the SPE peak $\sigma$ times a free parameter that will be named `sqrt2`, let's see how close it will be.
  * Usually, to account for the cases in which the electron misses the first dynode but still hits the second dynode giving rise to a signal that is under-amplified, a exponential decay o something else is added as a tail at the right side of the pedestal. Here, optionally, another Gaussian is used (a better option should be found), with the mean and the $\sigma$ modelled in reference to the SPE peak. Check for `--ADAPT HERE--` in the comment fields of the code

The ROOFIT tool is used to describe the model of the spectrum (it allows to keep separate shape parameters and counts of the components of the model) and to get a better guidance in the fit process (but under the hood the minimizer is always MINUIT).


In [38]:
RooWorkspace wb{"wb"};                 
// The ROOFIT workspace makes the declaration of the components more compact (instead of
// declaring each variable and parameter and each component and composite PDF), at the cost
// of learning the its own syntax in the factory() method

//
// The next lines declare the various Gaussian PDFs and its variables/parameters. Variables 
// with the same name in the same workspace are the same
//
wb.factory("Gaussian::ped(q[0,-5e6, 45e6],pedmean[0.],pedsigma[1.e6,0.,3.e6])");
wb.factory("Gaussian::one(q,gain[6.e6,1.e6,50e6],gainsigma[4.e6,1.e6,10.e6])");
//wb.factory("Gaussian::two(q,expr('gain*2',gain),expr('gainsigma*sqrt(2)',gainsigma))");
wb.factory("Gaussian::two(q,expr('gain*2',gain),"
                           "expr('gainsigma*sqrt2',gainsigma,sqrt2[1.41,0.1,10.]))");
wb.factory("Gaussian::d2(q,"
                       "expr('gain*d1gain',gain,d1gain[0.1,0.01,0.3]),"
                       "expr('gainsigma*d1gainsigma',gainsigma, d1gainsigma[0.5, 0.01, 1]))");
//wb.factory("Exponential::d2exp(q,"
//                               "expr('gain*ratio',gain,ratio[100,1.,10000.]))");

//
// Now the composite model PDF is made combining the various components, each with a parameter,
// 'Zeros', 'Ones', 'Twos' and (optionally) 'D1miss', representating the best-fitting number of
// events of this component
//

// -- ADAPT HERE -- Model with or without the sub-amplification case due to first dynode miss
 wb.factory("SUM::model(Zeros[2e5,1e4,1e8]*ped,Ones[1e4,100,1e5]*one,Twos[200,1.,1e3]*two,D1miss[100,1.,1e5]*d2)" );
//wb.factory("SUM::model(Zeros[1e5,1e3,1e8]*ped,Ones[1e3,10,1e6]*one,Twos[10,0.,1e4]*two)" );
//wb.Print("t")

[#0] WARNING:InputArguments -- The parameter 'pedsigma' with range [0, 3e+06] of the RooGaussian 'ped' exceeds the safe range of (0, inf). Advise to limit its range.


In [39]:
// Extract the needed variables out of the workspace (the access via namespace reported in the manual does not work) 
auto model = wb.pdf("model");
auto q = wb.var("q");
//model->Print("t");
//q->Print("v")

In [40]:
// Obtain the "ROOFIT version" of the ROOT TH1D
RooDataHist spe("SPE","Single photon charge spectrum",*q,&h1ch1q) ;

You might need to adapt the fit range. Check the fit output if there are errors

In [ ]:
// Do the fit and report results
std::unique_ptr<RooFitResult> roofitres{
    model->fitTo(spe, RooFit::Save(), RooFit::Range(-1e6,40e6))
};

/*if (list_setup_and_results["LED"] == 1.) {
    roofitres = std::make_unique<RooFitResult>(
        model->fitTo(spe, RooFit::Save(), RooFit::Range(-1e6,40e6))  //--ADAPT HERE--
    );
}*/

##### SPE fit results

The histogram is plotted again together with the fit results. Check the components of the model. Depending on the presence of 
the optional "first dynode skip" component in the model, you have to comment or uncomment the line with `--ENABLE HERE--` 

In [42]:
if (list_setup_and_results["LED"] == 1.) {
    c1.Clear();
    RooPlot *qframe = q->frame();
    spe.plotOn(qframe);
    model->plotOn(qframe);
    model->plotOn(qframe, RooFit::Components("ped"), RooFit::LineStyle(kDotted), RooFit::LineColor(kCyan));
    model->plotOn(qframe, RooFit::Components("one"), RooFit::LineStyle(kDashed), RooFit::LineColor(kRed));
    model->plotOn(qframe, RooFit::Components("two"), RooFit::LineStyle(kDotted), RooFit::LineColor(kOrange));
    model->plotOn(qframe, RooFit::Components("d2"), RooFit::LineStyle(kDotted), RooFit::LineColor(kViolet)); //--ENABLE HERE--
    qframe->SetMinimum(0.2); qframe->SetMaximum(qframe->GetMaximum()*2.); qframe->Draw();
    c1.Draw(); c1.SetLogy(true);
}

In [ ]:
// Collect the fit results for saving to JSON file
if (list_setup_and_results["LED"] == 1.) {
    for ( const auto& j : roofitres->floatParsFinal() ) {
        auto jj = static_cast<RooRealVar*>(j);
        jj->Print();
        //fmt::print( "{} {} +/- {}\n" , jj->GetName(), jj->getVal(), jj->getError() );
        list_setup_and_results[ jj->GetName() ] = jj->getVal();
        list_setup_and_results[ std::string{jj->GetName()}+"_error" ] = jj->getError();
    }
}
list_setup_and_results

# Saving the results

A ROOT file with the baseline and the signal spectra as well as the `std::map` with data conditions and results are saved 

In [27]:
// Keep it to false until you are sure that you are saving the results

if (true) {
    std::string hv = std::to_string( list_setup_and_results["HV"] );
    std::string rootfilename = fmt::format( "{}_{:.3f}V_LED{}_spectra.root", 
                                            pmt_serial_code, 
                                            list_setup_and_results["HV"],
                                            list_setup_and_results["LED"]);
    
    //pmt_serial_code + "_" + hv + "_spectra.root" };
    TFile root_file{ rootfilename.c_str() , "create" };

    root_file.WriteObject( &h1ch1b , "h1baseline" );
    root_file.WriteObject( &h1ch1q , "h1signal" );
    root_file.WriteObject( &list_setup_and_results , "results" );

    root_file.ls();
}

TFile**		AGG001_0.860V_LED20_spectra.root	
 TFile*		AGG001_0.860V_LED20_spectra.root	
  KEY: TH1F	h1baseline;1	Integrated baseline
  KEY: TH1F	h1signal;1	Integrated charge spectrum
  KEY: map<string,double>	results;1	object title
